In [1]:
import pandas as pd
import os

from helpers import (
    get_combined_df,
    coalesce_columns,
    save_final_df_as_jsonl,
    handle_slug_column_mappings,
)

In [2]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "for_sale_listings/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [3]:
exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

slug_column_mappings = {
    "_mlp_": "Median Listing Price",
    "_new_listings_": "New Listings",
    "new_pending": "New Pending",
}


data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        # ignore monthly data for now since it is redundant
        if "month" in filename:
            continue

        if "sfrcondo" in filename:
            cur_df["Home Type"] = "all homes"
        elif "sfr" in filename:
            cur_df["Home Type"] = "SFR"
        elif "condo" in filename:
            cur_df["Home Type"] = "condo/co-op only"

        data_frames = handle_slug_column_mappings(
            data_frames, slug_column_mappings, exclude_columns, filename, cur_df
        )


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "SizeRank",
        "RegionName",
        "RegionType",
        "StateName",
        "Home Type",
        "Date",
    ],
)

combined_df = coalesce_columns(combined_df)

combined_df

processing Metro_new_pending_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_month.csv
processing Metro_mlp_uc_sfr_sm_month.csv
processing Metro_new_pending_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfr_sm_week.csv
processing Metro_mlp_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_month.csv
processing Metro_mlp_uc_sfr_month.csv
processing Metro_new_listings_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_week.csv
processing Metro_new_listi

RegionID  SizeRank     RegionName RegionType StateName  Home Type  \
0         102001         0  United States    country       NaN        SFR   
1         102001         0  United States    country       NaN        SFR   
2         102001         0  United States    country       NaN        SFR   
3         102001         0  United States    country       NaN        SFR   
4         102001         0  United States    country       NaN        SFR   
...          ...       ...            ...        ...       ...        ...   
578648    845172       769   Winfield, KS        msa        KS  all homes   
578649    845172       769   Winfield, KS        msa        KS  all homes   
578650    845172       769   Winfield, KS        msa        KS  all homes   
578651    845172       769   Winfield, KS        msa        KS  all homes   
578652    845172       769   Winfield, KS        msa        KS  all homes   

              Date  Median Listing Price  Median Listing Price (Smoothed)  \
0       2018-01-13              259000.0                              NaN   
1       2018-01-20              259900.0                              NaN   
2       2018-01-27              259900.0                              NaN   
3       2018-02-03              260000.0                         259700.0   
4       2018-02-10              264900.0                         261175.0   
...            ...                   ...                              ...   
578648  2023-12-09              134950.0                         138913.0   
578649  2023-12-16              120000.0                         133938.0   
578650  2023-12-23              111000.0                         126463.0   
578651  2023-12-30              126950.0                         123225.0   
578652  2024-01-06              128000.0                         121488.0   

        New Pending (Smoothed)  New Listings  New Listings (Smoothed)  \
0                          NaN           NaN                      NaN   
1                          NaN           NaN                      NaN   
2                          NaN           NaN                      NaN   
3                          NaN           NaN                      NaN   
4                          NaN           NaN                      NaN   
...                        ...           ...                      ...   
578648                     NaN           NaN                      NaN   
578649                     NaN           NaN                      NaN   
578650                     NaN           NaN                      NaN   
578651                     NaN           NaN                      NaN   
578652                     NaN           NaN                      NaN   

        New Pending  
0               NaN  
1               NaN  
2               NaN  
3               NaN  
4               NaN  
...             ...  
578648          NaN  
578649          NaN  
578650          NaN  
578651          NaN  
578652          NaN  

[578653 rows x 13 columns]

In [4]:
# Adjust column names
final_df = combined_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df

Region ID  Size Rank         Region Region Type State  Home Type  \
0          102001          0  United States     country   NaN        SFR   
1          102001          0  United States     country   NaN        SFR   
2          102001          0  United States     country   NaN        SFR   
3          102001          0  United States     country   NaN        SFR   
4          102001          0  United States     country   NaN        SFR   
...           ...        ...            ...         ...   ...        ...   
578648     845172        769   Winfield, KS         msa    KS  all homes   
578649     845172        769   Winfield, KS         msa    KS  all homes   
578650     845172        769   Winfield, KS         msa    KS  all homes   
578651     845172        769   Winfield, KS         msa    KS  all homes   
578652     845172        769   Winfield, KS         msa    KS  all homes   

              Date  Median Listing Price  Median Listing Price (Smoothed)  \
0       2018-01-13              259000.0                              NaN   
1       2018-01-20              259900.0                              NaN   
2       2018-01-27              259900.0                              NaN   
3       2018-02-03              260000.0                         259700.0   
4       2018-02-10              264900.0                         261175.0   
...            ...                   ...                              ...   
578648  2023-12-09              134950.0                         138913.0   
578649  2023-12-16              120000.0                         133938.0   
578650  2023-12-23              111000.0                         126463.0   
578651  2023-12-30              126950.0                         123225.0   
578652  2024-01-06              128000.0                         121488.0   

        New Pending (Smoothed)  New Listings  New Listings (Smoothed)  \
0                          NaN           NaN                      NaN   
1                          NaN           NaN                      NaN   
2                          NaN           NaN                      NaN   
3                          NaN           NaN                      NaN   
4                          NaN           NaN                      NaN   
...                        ...           ...                      ...   
578648                     NaN           NaN                      NaN   
578649                     NaN           NaN                      NaN   
578650                     NaN           NaN                      NaN   
578651                     NaN           NaN                      NaN   
578652                     NaN           NaN                      NaN   

        New Pending  
0               NaN  
1               NaN  
2               NaN  
3               NaN  
4               NaN  
...             ...  
578648          NaN  
578649          NaN  
578650          NaN  
578651          NaN  
578652          NaN  

[578653 rows x 13 columns]

In [5]:
save_final_df_as_jsonl(FULL_PROCESSED_DIR_PATH, final_df)